---

# S05E05 : Deeper into classes & OOP - complex inheritance

Cyril Desjouy

--- 

## 1. Introduction

We saw in the previous notebook the simple inheritance. Python also supports more complex inheritance schemes. In OOP, there are 5 types of inheritance that are all supported by Python and schematized below:

* ***Single inheritance:*** *A single class inherits from another.*
```                                            
                            ┌──────────────┐       ┌──────────────┐
                            │  Base class  ╞═══>═══╡   Subclass   │
                            └──────────────┘       └──────────────┘
``` 
* ***Multilevel inheritance:*** *One class inherits from another which in turn inherit from another...*

```                                            
                   ┌──────────────┐       ┌──────────────┐       ┌──────────────┐
                   │  Base class  ╞═══>═══╡   Subclass   ╞═══>═══╡   Subclass   │     
                   └──────────────┘       └──────────────┘       └──────────────┘
``` 
* ***Hierarchical inheritance:*** *More than one class inherits from a base class.*
```
                                                   ┌──────────────┐
                                          ╔════>═══╡   Subclass   |
                            ┌─────────────╨┐       └──────────────┘
                            │  Base class  │       
                            └─────────────╥┘       ┌──────────────┐
                                          ╚════>═══╡   Subclass   |
                                                   └──────────────┘
```     
* ***Multiple inheritance:*** *One class inherits from multiple classes.*

```
                            ┌──────────────┐
                            |  Base class  ╞═════>════╗
                            └──────────────┘         ┌╨─────────────┐
                                                     │  Base class  │ 
                            ┌──────────────┐         └╥─────────────┘
                            |  Base class  ╞═════>════╝
                            └──────────────┘
``` 
* ***Hybrid inheritance:*** *It is a combination of at least two kind of inheritance.*


## 2. The ***mro***  algorithm

When a class inherits several classes, it is a question of determining the order in which the inheritance is made. To do this, Python uses an algorithm called ***mro*** for ***Multiple Resolution Order*** which takes care of that for us.

To illustrate this concept, let us consider the following basic class:

In [4]:
class Animal:
    legs = 4
    
    @classmethod
    def count_legs(cls):
        print(cls.legs, 'legs')

The output of the ***mro()*** of this class is as follows:
```
>> Animal.mro()
[__main__.Animal, object]
```
This object lists the order in which the attributes are to be resolved during inheritance. When the Python interpreter searches for an attribute, it first searches the first ***namespace*** listed by ***mro()***. If he doesn't find it in this ***namespace***, then he looks for it in the next one, and so on. 

Now consider the following **multilevel inheritance*** (***multilevel inheritance***):

In [5]:
class Turtle(Animal):
    attribute = 'shell'
    
class NinjaTurtle(Turtle):
    legs = 2

The results of the ***mro()*** for each of the subclasses are as follows:
```python
>> Turtle.mro()
[__main__.Turtle, __main__.Animal, object]
>> NinjaTurtle.mro()
[__main__.NinjaTurtle, __main__.Turtle, __main__.Animal, object]
```

When the `count_legs` method is called from the `Turtle` subclass, the Python interpreter looks in the ***namespace*** of `Turtle` for a method named `count_legs`, but does not find it. He then consults the ***mro*** and searches the next ***namespace***, the one of `Animal` where he finds `count_legs`.

When the `count_legs` method is called from the subclass `NinjaTurtle`, the Python interpreter looks in the ***namespace*** of `Turtle` for a method named `count_legs`, but does not find it. He then consults the ***mro*** and searches the next ***namespace***, the one of `Turtle` where he can't find it either. He ends up finding `count_legs` in the next ***namespace***, the one of `Animal`.

Both `Turtle` and `NinjaTurle` therefore inherit the class method `count_legs` defined in the base class `Animal`: 
```python
>> Animal.count_legs()           # Returns 4
>> Turtle.count_legs()           # Returns 4
>> NinjaTurtle.count_legs()      # Returns 2
```
The same procedure is applied to the class attribute `legs`. When calling `count_legs` from `Turtle`, the Python interpreter searches the ***namespace*** running `legs` but does not find it. He searches in the next ***namespace***, the one of `Animal` where he finds it. Similarly, when calling `count_legs` from `NinjaTurle`, the Python interpreter searches the current ***namespace*** and finds `legs`.

In this simple case, there is no real ambiguity. `NinjaTurle` inherits from `Turtle` which inherits from `Animal` (which inherits from `object`), but in more complex cases, it will be necessary to refer to the ***mro*** which conditions the search for attributes in the hierarchy of the classes it defines. 

## 2. ***super(subclass, instance of the subclass)***

We saw in the previous notebook how to use `super()` to call a method of a superclass from a subclass. We then used it without argument. It is also possible to provide two input arguments: 
```
super(subclass, instance of the subclass)
```
In the case where `super()` is used without an input argument, it defaults to the current class and instance. In the case of complex inheritances, it may be interesting to specify which sub-class to reference in order to reach a particular class. Consider the following **multiple inheritance** example:

In [65]:
class Ninja:
    def __init__(self, weapon='nunchaku'):
        self.weapon = weapon
        
class Turtle:
    def __init__(self):
        self.armor = 'shell'
        
class NinjaTurtle(Ninja, Turtle):
    def __init__(self, weapon=None):
        super().__init__(weapon)           # Equivalent à super(NinjaTurtle, self).__init__(weapon)
        self.battlecry = 'cowabunga'

In the case of **multiple inheritance**, the different base classes are simply separated by commas. The result of ***mro()*** for `NinjaTurtle` is as follows:
```python
>> NinjaTurtle.mro()
[__main__.NinjaTurtle, __main__.Ninja, __main__.Turtle, object]
```

The `__init__` method of `Ninja` is called from the `__init__` method of `NinjaTurtle`. It is indeed the first in the ***mro()******* after the current class** ( `NinjaTurtle`):
```python
>> donatello = NinjaTurtle(weapon='staff')
>> vars(donatello)
{'weapon': 'staff', 'battlecry': 'cowabunga'}
 ```
`NinjaTurtle` does inherit the instance attribute `weapon` but no `armor`. In order for it to also retrieve the instance attributes of `Turtle`, you must use `super` again:

In [69]:
class NinjaTurtle(Ninja, Turtle):
    def __init__(self, weapon=None):
        super(NinjaTurtle, self).__init__(weapon)   # Equivalent to Ninja.__init__(self, weapon)
        super(Ninja, self).__init__()               # Equivalent to Turtle.__init__(self)
        self.battlecry = 'cowabunga'

`NinjaTurtle` is then initialized with the `__init__` method of `Ninja` then of `Turtle` and thus retrieves the instance attributes declared in these methods:
```python
>> donatello = NinjaTurtle(weapon='staff')
>> vars(donatello)
{'weapon': 'staff', 'armor': 'shell', 'battlecry': 'cowabunga'}
```
You will notice that the class provided as an input argument to `super()` must be the previous class according to `mro()` the class to be reached.

## Quizz

<div class="alert alert-block alert-info">
Without implementing the following classes, try to determine using the results of the mro():
    <ul>
    <li> What is the attribute <code>armor</code> worth in <code>NinjaTurtle1</code> ? in <code>NinjaTurtle2</code>? </li>
    <li> What is the attribute <code>weapon</code> worth in <code>NinjaTurtle1</code> ? in <code>NinjaTurtle2</code> ?</li>
    </ul>
</div>

```python
class Human:
    weapon = 'intelligence'
    armor = 'clothes'
    
class Animal:
    weapon = 'instinct'
    
class Ninja(Human):
    weapon = 'nunchaku'
    
class Turtle(Animal):
    armor = 'shell'
    
class NinjaTurtle1(Ninja, Turtle):
    pass

class NinjaTurtle2(Turtle, Ninja):
    pass
```


```python
>> NinjaTurtle1.mro()
[__main__.NinjaTurtle1,
 __main__.Ninja,
 __main__.Human,
 __main__.Turtle,
 __main__.Animal,
 object]

>> NinjaTurtle2.mro()
[__main__.NinjaTurtle2,
 __main__.Turtle,
 __main__.Animal,
 __main__.Ninja,
 __main__.Human,
 object]
```